
# Cap Recognizer
The goal of this project is to classify 20 different types of caps / headwears commonly worn around the world. The types are following: <br/>
1. baseball cap
2. beanie cap
3. fedora cap
4. cowboy hat
5. kepi cap
6. flat cap
7. trucker cap
8. newsboy cap
9. pork pie hat
10. bowler hat
11. top hat
12. sun hat
13. boater hat
14. ivy cap
15. bucket hat
16. balaclava cap
17. turban cap
18. taqiyah cap
19. rasta cap
20. visor cap

# Setting Up Necessary Things

In [1]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline 
bs = 32 # batch size 
version = 1

In [ ]:
!pip install -Uqq fastai

In [2]:
from fastai import *
from fastai.vision.all import *
from fastai.vision.widgets import *

# Fetch Data

In [3]:
data_path = "data1220"
dblock = DataBlock(
    blocks=(ImageBlock, CategoryBlock), 
    get_items=get_image_files,                        # get_image_files returns a list of all images in that path recursively by default
    splitter=RandomSplitter(valid_pct=0.1, seed=42),  # getting 90-10 train-validation split
    get_y=parent_label,                               # taking the folder name as labels
    item_tfms=Resize(128))                            # resizing to get the image of same shape

In [16]:
dblock = dblock.new(item_tfms=RandomResizedCrop(224, min_scale=0.5), batch_tfms=aug_transforms())
dls = dblock.dataloaders(data_path, bs = bs)
torch.save(dls, f"disease.pkl")

TypeError: 'NoneType' object is not iterable

In [10]:
dls = torch.load(f"disease.pkl")

FileNotFoundError: [Errno 2] No such file or directory: 'disease.pkl'

In [5]:
dls.train.show_batch(max_n=8, nrows=2)

NameError: name 'dls' is not defined

In [6]:
dls.valid.show_batch(max_n=8, nrows=2)

NameError: name 'dls' is not defined

# Training and Data Cleaning

In [12]:
model_path = "models"

In [13]:
model = vision_learner(dls, resnet34, metrics=[error_rate,accuracy])

NameError: name 'dls' is not defined

In [ ]:
model.fine_tune(0)

In [11]:
model.fine_tune(1)

NameError: name 'model' is not defined

In [ ]:
from fastai.vision.all import *

# Load your data and create your dataloaders
# ...

# Define your VGG16_bn model

# Find the optimal learning rate
lr_min, lr_steep = model.lr_find()

# Use the One-Cycle Policy for training
model.fit_one_cycle(10, lr_max=lr_steep)

# Perform hyperparameter tuning
hyper_params = {
    'weight_decay': [1e-4, 1e-3, 1e-2],
    'ps': [0.1, 0.2, 0.3],
    'lr': [lr_min, lr_steep]
}

best_accuracy = 0.0
best_hyperparams = None

for wd in hyper_params['weight_decay']:
    for p in hyper_params['ps']:
        for lr in hyper_params['lr']:
            model = cnn_learner(dls, vgg16_bn, metrics=accuracy, wd=wd, ps=p)
            model.fit_one_cycle(10, lr_max=lr)
            accuracy = model.validate()[1]
            print(f"Weight Decay: {wd}, Dropout: {p}, Learning Rate: {lr}, Accuracy: {accuracy}")

            if accuracy > best_accuracy:
                best_accuracy = accuracy
                best_hyperparams = {'weight_decay': wd, 'ps': p, 'lr': lr}

print("Best Hyperparameters:", best_hyperparams)


In [ ]:
from fastai.vision.all import *
# Load your data and create your dataloaders
# ...
# Define your hyperparameters
hyper_params = {
    'weight_decay': 1e-4,
    'ps': 0.2,
    'lr': 1e-3
}
#
# Define your model and train it with the hyperparameters
model = cnn_learner(dls, vgg16_bn, metrics=accuracy, wd=hyper_params['weight_decay'], ps=hyper_params['ps'])
model.fit_one_cycle(10, lr_max=hyper_params['lr'])

# Evaluate the model on the validation or test dataset
accuracy = model.validate()[1]
print("Accuracy:", accuracy)

In [ ]:
model.save(f"sharar420")

In [ ]:
model.load(f"sharar420")

In [ ]:
interp = ClassificationInterpretation.from_learner(model)
interp.plot_confusion_matrix()

In [ ]:
interp.plot_top_losses(9, nrows=3)

In [ ]:
cleaner = ImageClassifierCleaner(model)
cleaner # flat cap, bucket hat, taqiyah cap

In [ ]:
for idx in cleaner.delete(): cleaner.fns[idx].unlink()                                    # delete irrelevant data
for idx,cat in cleaner.change(): hutil.move(str(cleaner.fns[idx]), f"{data_path}/{cat}") # change the directory

# Export model for inference

In [ ]:
model.export(f"models/aircraft.pkl")